In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import glob
import json
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer

In [2]:
import sys
sys.path.append("..")

from Tools.Emoji_Distance import sentiment_vector_to_emoji
from Tools.Emoji_Distance import emoji_to_sentiment_vector

def emoji2sent(emoji_arr):
    return np.array([emoji_to_sentiment_vector(e) for e in emoji_arr])

def sent2emoji(sent_arr):
    return [sentiment_vector_to_emoji(s) for s in sent_arr]

In [3]:
SINGLE_LABEL = True

# simple twitter approach
*for learning emoji usage by single (in the meaning of unconnected) twitter messages*

## loading train data

In [4]:
data_root_folder = "./data_en/" # i created a symlink here

* get all json files in `data_root_folder`

In [5]:
json_files = sorted(glob.glob(data_root_folder + "/*.json"))

----

* so far, only load the first file

In [6]:
twitter_data = pd.read_json(json_files[0], encoding="utf-8")
twitter_data

EMOJI  \
0                           [🔥, 👏]   
1                              [🤦]   
2                              [😄]   
3                              [📷]   
4                           [😩, 😩]   
5                           [😭, 💓]   
6                              [😂]   
7                              [💯]   
8                              [🙄]   
9                        [😟, 😥, 😢]   
10                             [🌻]   
11                       [🍁, 🌺, 🍂]   
12                             [🍃]   
13                          [💭, 🤦]   
14                          [😍, 😘]   
15                             [😜]   
16                          [😂, 🔥]   
17                             [💕]   
18                             [😉]   
19                             [👅]   
20                          [👌, 🙂]   
21                          [🤗, 📺]   
22                             [💯]   
23                       [👅, 💦, 🍑]   
24                             [💔]   
25                       [🤐, 🤐, 🤐]   
26                             [😴]   
27                             [😂]   
28                          [😂, 🙄]   
29              [🎉, 🎂, 🎈, 🎊, 🎁, 💜]   
...                            ...   
68703                          [😕]   
68704                       [😂, 😩]   
68705                          [😂]   
68706                          [💖]   
68707                 [🌆, 👉, 🚖, 📞]   
68708                          [😁]   
68709                          [😋]   
68710                    [👌, 🎃, 😘]   
68711                          [👍]   
68712                          [😭]   
68713                          [😂]   
68714                    [😭, 😭, 💘]   
68715                       [😫, ✋]   
68716                       [😂, 🙁]   
68717                          [😭]   
68718                       [😢, 💔]   
68719                          [🙃]   
68720              [😂, 😂, 😂, 😂, 😂]   
68721                    [👌, 👊, 🙌]   
68722                          [😴]   
68723                 [😂, 😂, 😂, 😂]   
68724                          [😀]   
68725                          [😎]   
68726                          [✨]   
68727                          [🤷]   
68728                          [😘]   
68729                          [😂]   
68730                          [🙏]   
68731                          [💁]   
68732  [🍃, 🌻, 🌻, 🍃, 🍃, 💐, 💐, 🍃, 🙋]   

                                              HASHTAGS  \
0                                                   []   
1                                                   []   
2                                                   []   
3                                                   []   
4                                                   []   
5                                                   []   
6                                                   []   
7                                                   []   
8                                                   []   
9                                                   []   
10                                                  []   
11                                                  []   
12         [#mortdale, #partofthefamily, #gorgeousboy]   
13                                                  []   
14                                     [#7YearsOfKMH2]   
15                                                  []   
16                                                  []   
17                                                  []   
18                                                  []   
19                                 [#footfetishnation]   
20                                                  []   
21                                                  []   
22                                                  []   
23                                                  []   
24                                                  []   
25                                                  []   
26                                                  []   
27                                              

* extracting emojis and text

In [37]:
emojis = twitter_data['EMOJI']
plain_text = twitter_data['text']

* make our plain text more "plain":
    * removing the keyword `<EMOJI>` (just for the beginning)
    * removing remaining useless emojis, like skin modifier etc.

In [38]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

In [39]:
# filtering them and the EMOJI keyword out:
plain_text = plain_text.str.replace("<EMOJI>","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")

* defining different criterias for choosing a single emoji (currently `latest` is used)

In [40]:
def latest(lst):
    return lst[-1] if len(lst) > 0 else 'X' 
def most_common(lst):
    # trying to find the most common used emoji in the given lst
    return max(set(lst), key=lst.count) if len(lst) > 0 else "X" # setting label to 'X' if there is an empty emoji list

* convert all emojis to a sentiment vector

In [41]:
labels = emoji2sent([latest(e) for e in emojis])


In [42]:
len(labels)

68733

In [43]:
wrong_labels = np.isnan(np.linalg.norm(labels, axis=1))

* remove all data we have no label for

In [44]:
labels = labels[np.invert(wrong_labels)]
plain_text = plain_text[np.invert(wrong_labels)]
emojis = emojis[np.invert(wrong_labels)]

In [45]:
print(len(labels), len(emojis), len(plain_text))

58308 58308 58308


* generate weights:

In [46]:
# at first count over our table
emoji_count = {}


for e_list in emojis:
    for e in set(e_list):
        if e not in emoji_count:
            emoji_count[e] = 0
        emoji_count[e] += 1

emoji_count
emoji_sum = sum([emoji_count[e] for e in emoji_count])

emoji_weights = {}
for e in emoji_count:
    # tfidf for emojis
    emoji_weights[e] = np.log((emoji_sum / emoji_count[e]))

weights_sum= sum([emoji_weights[x] for x in emoji_weights])
    
# normalize:
for e in emoji_weights:
    emoji_weights[e] = emoji_weights[e] / weights_sum

emoji_weights['X'] = 0  # dummy values
emoji_count['X'] = 0

* generating train and test set:

In [49]:
X1, Xt1, y1, yt1 = train_test_split(plain_text, labels, test_size=0.1, random_state=4222)

In [50]:
#y1_weights = np.array([(sum([emoji_weights[e] for e in e_list]) / len(e_list)) if len(e_list) > 0 else 0 for e_list in sent2emoji(y1)])

In [51]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

* train. this can take a very long time...

In [52]:
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.multiclass import OneVsRestClassifier as OVRC
from sklearn.tree import DecisionTreeClassifier as DTC

from keras.models import Sequential
from keras.layers import Dense

/home/jonas/.local/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [53]:
def train(max_size = 10000, layers=[(1024, 'relu'),(y1[0].shape[0],'softmax')], random_state=4222, ovrc=False, n_iter=5):
    
    model = Sequential()
    
    # build mlp layers:
    keras_layers = []
    first_layer = True
    for layer in layers:
        if first_layer:
            model.add(Dense(units=layer[0], activation=layer[1], input_dim=vectorizer.transform([" "])[0]._shape[1]))
            first_layer = False
        else:
            model.add(Dense(units=layer[0], activation=layer[1]))
    
    #mlp = MLPClassifier(layers=sknn_layers, random_state=random_state, verbose=True, n_iter=n_iter, batch_size=100)
    
    model.compile(loss='categorical_crossentropy',
              optimizer='sgd',
              metrics=['accuracy'])
    
    clf = OVRC(model) if ovrc else model

    clf.fit(vec_train[:max_size].A, y1[:max_size], validation_split=0.2)#, sample_weight=y1_weights[:max_size])
    
    return clf

In [54]:
clf = train(max_size=10000,layers=[(1200, 'relu'),(1200,'relu'),(y1[0].shape[0],'softmax')])

Train on 8000 samples, validate on 2000 samples
Epoch 1/1
8000/8000 [==============================] - 80s 10ms/step - loss: 1.0421 - acc: 0.7270 - val_loss: 1.0213 - val_acc: 0.7330


In [55]:
X1

10237    <USER> <USER> How much do you know about the y...
45851               She said she don't start until Friday 
28327    Ryane just told me to not stress because it's ...
22017    Meet Asian &amp; Russian Beauty From Here   Fi...
23341                                      What do u mean 
42942    ┊ <HASHTAG>  <USER> ┊<HASHTAG> ✲～┊ <HASHTAG> ✲...
28320                                 Woot woot leafs win 
26801    <USER> we’re here for you and you know that, y...
66054               <USER> gm Mailand have an awesome day 
64440                                     Happy halloween 
1695                                BARCELONA SPOING CLUB 
57848    I will purchase a few things because I love th...
6174                    <USER> Ah I'll let you off then ! 
9295     <USER> just the idea of empowering women is so...
48858    Damn!! People late on the <USER> thing. This t...
17032                                     <USER> I miss u 
30856                   I just want to be with you alway

* make a prediction and store it in a csv file:

In [56]:
pred = clf.predict(vectorizer.transform(Xt1))

In [57]:
pred

array([[0.49225155, 0.22154534, 0.28620324],
       [0.4917669 , 0.22080076, 0.28743234],
       [0.49208197, 0.22085808, 0.28705996],
       ...,
       [0.48990184, 0.22155353, 0.28854463],
       [0.49245682, 0.22013731, 0.28740585],
       [0.4891684 , 0.2214878 , 0.2893438 ]], dtype=float32)

In [59]:
# build a dataframe to visualize test results:
testlist = pd.DataFrame({'text': Xt1, 
                         'teacher': sent2emoji(yt1),
                         'predict': sent2emoji(pred)})

In [60]:
display(testlist)


predict teacher                                               text
62474       😂       🙋                                           Lovely  
11750       😂       😂  ☝ child they told that to slaves and look what...
316         😂       😂                                Only in Wisconsin  
33553       😂       🙏            : Barboursville  For Taxi 703-445-4450 
1566        😂       😏                                  who cares anyway 
54842       😂       😭  <USER> first it was spratt then faze spratt th...
16711       😂       😚  I will forever love the Dodgers! BLEED BLUE  t...
52129       😂       😊                             ok she nailed this ‍️ 
66914       😂       🙆             time to create the Christmas playlist 
42046       😂       😍  Penultimate <HASHTAG> of the 2017 race season!...
13783       😂       😊  hey friends i need space 2nite. happy 11-1! lo...
4034        😂       😒  Sombitch! 3.5 secs left an the goddamn 2K serv...
9773        😂       😏                                  sounds great..   
27593       😂       😴         what happens after I give babe a massage  
22601       😂       🙏                                  <USER> Thank you 
64332       😂       😚            <USER> I love you  I'm so proud of you 
23677       😂       🙋  <USER> <USER> Love how your coffee bags pop up...
1530        😂       😭                                     <USER> I know 
38375       😂       😏  <USER> Xmas songs all the way! I got a new chr...
37403       😂       🙆                         54 days until Christmas!! 
52706       😂       🙏  "November comesAnd November goes, With the las...
9628        😂       😭                          <USER> You want me dead  
41270       😂       😍  Finally arrived  Thank you so much <USER>  So ...
56276       😂       😂                             Omfg this is amazing  
14805       😂       😊                  Finding my <HASHTAG> need it now 
1275        😂       😊                              <USER> happy birthday
30821       😂       😌  <USER> better stock up, quenouille season is c...
36974       😂       😂  i always think miguel is saying "black power" ...
31270       😂       😚                                   <USER> so proud 
21672       😂       😭                           <USER> snapchat chick ? 
...       ...     ...                                                ...
6464        😂       😂  <USER> <USER> Actually I don’t think that woul...
14439       😂       😛  happy birthday to a really great friend, hope ...
30789       😂       😏  Might fuck around and not turn in my library b...
37129       😂       😀  My lil baby sick and it’s making me sad, I den...
61305       😂       😃  Love our customers...always on the go! ❤️  TRO...
4821        😂       🙌                      God bless whoever you marry! 
6509        😂       😸   j-u-v-e: On 1 November, Juventus turns 120! H...
41347       😂       😊  <USER> Yeah, sunshine, I promise  I love you a...
15368       😂       🙌  You ain't ever made love, You just wanted some...
22594       😂       😂            This whole lingerie thing is funny sha 
61471       😂       😚                       <USER> Wooo  congrats buddy!
63724       😂       😉                                    Early mornings 
7399        😂       😭                              <USER> <USER> So Sad 
8262        😂       😀  But opening up means trusting others.And that'...
61430       😂       😚                                 bambam pink hair❤️
59747       😂       😂  Nah last nights game was well worth my months ...
47655       😂       😚  <USER> wish your many more happy returns of th...
30992       😂       😶  my heart breaks into a million pieces every mo...
2204        😂       🙏  Call Congress (202) 224-3121 <HASHTAG> <HASHTA...
41224       😂       😂     I love Lucas’s sister! ❤️ Erica is so funny!  
65180       😂       😁                        <USER> PULL THRU JELLYBEAN 
48319       😂       😭  i miss the snickerdoodle swirl from <USER> so ...
19825       😂       😋                      I love you- and I rea

In [61]:
testlist.to_csv('test.csv')

* a simple output widget for testing:

In [63]:
out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        pred = clf.predict(vectorizer.transform([t.value]))
        
        display(Markdown("# " + str(sent2emoji(pred))))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

VBox(children=(Button(description='get smiley', icon='check', style=ButtonStyle(), tooltip='Click me'), Output()))

In [ ]:
import numpy as np

y_trans = mlb.inverse_transform(yt1)
pred_trans = mlb.inverse_transform(yt1)

# evaluate accuracy
pos = 0
neg = 0
all = 0
for entry in range(len(y_trans)):
    if len(np.intersect1d(y_trans[entry], pred_trans[entry])) > 0:
        pos += 1
    else:
        neg += 1
    all += 1
print(pos/all)
print(neg)